# COVID-19 - Análise dos dados 
##  Para esta análise estão sendo usadas as bases de dados do COVID-19 fornecidas pela universidade [Johns Hopkins], serão usadas as bases de dados por categoria ( [Confirmed], [Recovered], [Deaths]) assim como a base de [reporte diario].

## As bases de dados  por categoria são composta por:
- Province/State - Província/estado que foi registrado a ocorrência
- Country/Region - Continente/região que foi registrado a ocorrência
- Lat - latitude da região
- Long - longitude da região
- data - colunas que representam a data diário das ocorrências

## A base de dados  de reporte diário é composta por:
- Province/State - Provincia/estado que foi registrado a ocorrência
- Country/Region - Continente/região que foi registrado a ocorrência
- Last Update - Data da última atualização
- Confirmed - Quantidade de casos confirmados
- Deaths - Quantidade de mortes
- Recovered - quantidade de recuperações
- Lat - latitude da região
- Long - longitude da região
- data - colunas que representam a data diário das ocorrências


### obs: todas as bases de dados usadas são atualizadas diariamente.


[Johns Hopkins]: <https://github.com/CSSEGISandData>
[Confirmed]: <https://github.com/CSSEGISandData/COVID-19/blob/master/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-Confirmed.csv>
[Recovered]: <https://github.com/CSSEGISandData/COVID-19/blob/master/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-Recovered.csv>
[Deaths]: <https://github.com/CSSEGISandData/COVID-19/blob/master/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-Deaths.csv>
[reporte diario]: <https://github.com/CSSEGISandData/COVID-19/tree/master/csse_covid_19_data/csse_covid_19_daily_reports>


In [1]:
# importes necessários
import pandas as pd
import altair as alt
import numpy as np
from datetime import date
from vega_datasets import data

In [2]:
# Constantes
prefixo_taxa = 'taxa_aumento_'
data_formato = '%m-%d-%Y'
data_atual = date.today()
data_atual_formatada = data_atual.strftime(data_formato)
data_ultima_checagem_confirmada = '03-21-2020'
URL_covid_confirmed_for_day = 'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/{0}.csv'

### Importe das báses de dados por categoria

In [3]:
covid_confirmed = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
covid_recovered = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')
covid_deaths = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
covid_deaths.head()

Province/State Country/Region      Lat     Long  1/22/20  1/23/20  1/24/20  \
0            NaN    Afghanistan  33.0000  65.0000        0        0        0   
1            NaN        Albania  41.1533  20.1683        0        0        0   
2            NaN        Algeria  28.0339   1.6596        0        0        0   
3            NaN        Andorra  42.5063   1.5218        0        0        0   
4            NaN         Angola -11.2027  17.8739        0        0        0   

   1/25/20  1/26/20  1/27/20  ...  3/19/20  3/20/20  3/21/20  3/22/20  \
0        0        0        0  ...        0        0        0        1   
1        0        0        0  ...        2        2        2        2   
2        0        0        0  ...        9       11       15       17   
3        0        0        0  ...        0        0        0        1   
4        0        0        0  ...        0        0        0        0   

   3/23/20  3/24/20  3/25/20  3/26/20  3/27/20  3/28/20  
0        1        1        2        4        4        4  
1        4        5        5        6        8       10  
2       17       19       21       25       26       29  
3        1        1        1        3        3        3  
4        0        0        0        0        0        0  

[5 rows x 71 columns]

## Importe da báse de dados de reporte diário, caso não seja encontrado a base relacionada ao dia atual será carregado uma base de data pré definida

In [4]:
covid_reports_for_day = []

try:
    covid_reports_for_day = pd.read_csv(URL_covid_confirmed_for_day.format(data_atual_formatada))
except:
    covid_reports_for_day = pd.read_csv(URL_covid_confirmed_for_day.format(data_ultima_checagem_confirmada))
    
covid_reports_for_day.tail()

Province/State         Country/Region          Last Update  Confirmed  \
299            NaN                 Jersey  2020-03-17T18:33:03          0   
300            NaN            Puerto Rico  2020-03-17T16:13:14          0   
301            NaN  Republic of the Congo  2020-03-17T21:33:03          0   
302            NaN            The Bahamas  2020-03-19T12:13:38          0   
303            NaN             The Gambia  2020-03-18T14:13:56          0   

     Deaths  Recovered  Latitude  Longitude  
299       0          0   49.1900     -2.110  
300       0          0   18.2000    -66.500  
301       0          0   -1.4400     15.556  
302       0          0   24.2500    -76.000  
303       0          0   13.4667    -16.600

### É criado uma base de dados para análise da série temporal a partir da união das bases de dados por categoria.

In [5]:
todal_casos_morte_por_dia = np.sum(covid_deaths.iloc[ : , 4 : covid_deaths.shape[1]])
todal_casos_confirmacao_por_dia = np.sum(covid_confirmed.iloc[ : , 4 : covid_confirmed.shape[1]])
todal_casos_recuperacao_por_dia = np.sum(covid_recovered.iloc[ : , 4 : covid_recovered.shape[1]])

covid_serie_temporal = pd.DataFrame([todal_casos_confirmacao_por_dia, todal_casos_recuperacao_por_dia, todal_casos_morte_por_dia]).T
covid_serie_temporal.reset_index(inplace = True)
covid_serie_temporal.columns = ['data','confirmacao', 'recuperacao', 'mortes']
covid_serie_temporal['data'] = pd.to_datetime(covid_serie_temporal['data'])

covid_serie_temporal.tail()

data  confirmacao  recuperacao  mortes
62 2020-03-24       418045       108000   18625
63 2020-03-25       467653       113787   21181
64 2020-03-26       529591       122150   23970
65 2020-03-27       593291       130915   27198
66 2020-03-28       660706       139415   30652

### Método ira criar uma nova coluna do dataset a partir de um prefixo e o nome da coluna, essa nova coluna representa a taxa de créscimento diário da coluna. A taxa de crescimento é cálculada pela seguinte fórmula:

\begin{align}
\text{taxa_crescimento} ={\frac  {({\text{valor_presente}})-({\text{valor_passado}})}{({\text{valor_passado}})}} 
\end{align}

In [6]:
def taxa_de_crescimento(data, colum):
    dimensao = data[colum].shape[0]
    resultados =[]
    for i in range (dimensao - 1):
        resultados.append(data[colum][i+1] - data[colum][i])
        if(i == dimensao - 2):
            resultados.append(np.nan)
        
    data[prefixo_taxa + colum] = resultados

### aplica o método `taxa_de_crescimento` aos campos da análise

In [7]:
taxa_de_crescimento(covid_serie_temporal, 'confirmacao')
taxa_de_crescimento(covid_serie_temporal, 'recuperacao')
taxa_de_crescimento(covid_serie_temporal, 'mortes')
covid_serie_temporal.tail()

data  confirmacao  recuperacao  mortes  taxa_aumento_confirmacao  \
62 2020-03-24       418045       108000   18625                   49608.0   
63 2020-03-25       467653       113787   21181                   61938.0   
64 2020-03-26       529591       122150   23970                   63700.0   
65 2020-03-27       593291       130915   27198                   67415.0   
66 2020-03-28       660706       139415   30652                       NaN   

    taxa_aumento_recuperacao  taxa_aumento_mortes  
62                    5787.0               2556.0  
63                    8363.0               2789.0  
64                    8765.0               3228.0  
65                    8500.0               3454.0  
66                       NaN                  NaN

### O gráfico demonstra a evolução dos casos de infecção pelo COVID-19, o gráfico inferior demonstra o comparativo de crescimento no decorrer do tempo para os casos de confirmação, recuperação e morte. Já os gráficos superiores demonstram a evolução de acordo com o respectivos status: confirmação, recuperação e morte. Sendo possível selecionar um período de tempo ao clicar e arrastar o mouse.

In [21]:
brush = alt.selection_interval(encodings=['x'])

card_principal = alt.Chart(covid_serie_temporal).mark_area(
    color="lightyellow",
    line=True
).encode(
    alt.X("data:T",),
    alt.Y('confirmacao:Q'),
    tooltip = ["data:T", 'confirmacao:Q']
).properties(width=800,height=200, title='Ocorrências do COVID-19 ao decorrer do tempo.').add_selection(brush)


confirmacao = alt.Chart(covid_serie_temporal).mark_area(
    color="lightyellow",
    line=True
).encode(
    alt.X("data:T", scale=alt.Scale(domain=brush)),
    alt.Y('confirmacao:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Casos confirmados de infecção', 'pelo COVID-19']).transform_filter(brush)

recuperacao = alt.Chart(covid_serie_temporal).mark_area(
    color="lightgreen",
    line=True
).encode(
    alt.X("data:T"),
    alt.Y('recuperacao:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Casos confirmados de recuperação', 'do COVID-19']).transform_filter(brush)

morte = alt.Chart(covid_serie_temporal).mark_area(
    color="red",
    line=True
).encode(
    alt.X("data:T"),
    alt.Y('mortes:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Casos confirmados de morte' ,'pelo COVID-19']).transform_filter(brush)

evolucao_COVID = (confirmacao | recuperacao | morte) & (card_principal.encode(alt.Y('confirmacao', title= 'Quantidade de pessoas')) + recuperacao + morte)

evolucao_COVID.save('plots/evolucao_COVID_19.html')

evolucao_COVID

alt.VConcatChart(...)

### O gráfico demonstra a taxa de crescimento dos casos de infecção pelo COVID-19, o gráfico inferior demonstra o comparativo de crescimento no decorrer do tempo para os casos de confirmação, recuperação e morte. Já os gráficos superiores demonstram a taxa de evolução de acordo com o respectivos status: confirmação, recuperação e morte. Sendo possível selecionar um período de tempo ao clicar e arrastar o mouse.

In [26]:
brush = alt.selection_interval(encodings=['x'])

card_principal = alt.Chart(covid_serie_temporal.dropna()).mark_area(
    color="lightyellow",
    line=True
).encode(
    alt.X("data:T",),
    alt.Y('taxa_aumento_confirmacao:Q'),
    tooltip = ["data:T", 'taxa_aumento_confirmacao:Q']
).properties(width=800,height=300, title='Taxa de crescimento do contágio pelo COVID-19 ao decorrer do tempo.').add_selection(brush)


confirmacao = alt.Chart(covid_serie_temporal.dropna()).mark_area(
    color="lightyellow",
    line=True
).encode(
    alt.X("data:T", scale=alt.Scale(domain=brush)),
    alt.Y('taxa_aumento_confirmacao:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Taxa de crescimento de casos', 'confirmados de infecção pelo COVID-19']).transform_filter(brush)

recuperacao = alt.Chart(covid_serie_temporal.dropna()).mark_area(
    color="lightgreen",
    line=True
).encode(
    alt.X("data:T"),
    alt.Y('taxa_aumento_recuperacao:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Taxa de crescimento de casos','confirmados de recuperação do COVID-19']).transform_filter(brush)

morte = alt.Chart(covid_serie_temporal.dropna()).mark_area(
    color="red",
    line=True
).encode(
    alt.X("data:T"),
    alt.Y('taxa_aumento_mortes:Q', title= 'Quantidade de pessoas')
).properties(width=200,height=200, title=['Taxa de crescimento de casos','confirmados de morte pelo COVID-19']).transform_filter(brush)

taxa_aumento_contagio = (confirmacao | recuperacao | morte) & (card_principal.encode(alt.Y('taxa_aumento_confirmacao', title= 'Quantidade de pessoas')) + recuperacao + morte)

taxa_aumento_contagio.save('plots/taxa_de_aumento_no_contagio_COVID_19.html')

taxa_aumento_contagio

alt.VConcatChart(...)

In [13]:
covid_reports_for_day.head()

Province/State Country/Region          Last Update  Confirmed  Deaths  \
0          Hubei          China  2020-03-21T10:13:08      67800    3139   
1            NaN          Italy  2020-03-21T17:43:03      53578    4825   
2            NaN          Spain  2020-03-21T13:13:30      25374    1375   
3            NaN        Germany  2020-03-21T20:43:02      22213      84   
4            NaN           Iran  2020-03-21T11:13:12      20610    1556   

   Recovered  Latitude  Longitude  
0      58946   30.9756   112.2707  
1       6072   41.8719    12.5674  
2       2125   40.4637    -3.7492  
3        233   51.1657    10.4515  
4       7635   32.4279    53.6880

### O mapa demonstra a situação de contágio pelo COVID-19 dos Países/Estados, podendo-se interagir com o mapa ao passar o mouse nas regiões em vermelho, onde irá ser demonstrado respectivamente:
- Quantidade de confirmações;
- Quantidade de mortes;
- Quantidade de recuperações;
- Província/Estado selecionado;
- País selecionado;
- Data da última atualização.


In [23]:
source = alt.topo_feature(data.world_110m.url, 'countries')
sphere = alt.sphere()
graticule = alt.graticule()

projections = 'equirectangular'

size = alt.Size('Confirmed:N', legend=None)

circles = alt.Chart(covid_reports_for_day).mark_circle(color='#FE2E2E', opacity = 0.4).encode(
    longitude="Longitude:Q",
    latitude="Latitude:Q",
    size = size,
    tooltip = ['Confirmed:Q', 'Deaths:Q', 'Recovered:Q', 'Province/State:N', 'Country/Region:N', 'Last Update:T']
)

geo_shape = alt.layer(
    alt.Chart(sphere).mark_geoshape(fill='lightblue', stroke = "invert ? '#777' : '#bbb'"),
    alt.Chart(graticule).mark_geoshape(stroke='white', strokeWidth=0),
    alt.Chart(source).mark_geoshape(fill='#F5F3A6', stroke='black') 
).properties(
    width=800,
    height=400
).project(projections).properties(title='Mapa mundi')

fig = alt.layer(
    geo_shape,
    circles,
)

fig.save('plots/situação_COVID_19.html')

fig

alt.LayerChart(...)

In [258]:
source = alt.topo_feature(data.world_110m.url, 'countries')

projections = 'equirectangular'

size = alt.Size('Confirmed:N', legend=None)

pontos = alt.Chart(covid_reports_for_day).mark_circle(color='#FE2E2E').encode(
    longitude="Long_:Q",
    latitude="Lat:Q",
    size = size,
    tooltip = ['Confirmed:N', 'Deaths', 'Recovered', 'Province_State', 'Country_Region', 'Last_Update']
)

base = alt.Chart(source).mark_geoshape(
    stroke='smolke',
).properties(
    width=800,
    height=400
).project(projections).properties(title='Mapa mundi')


base + pontos

alt.LayerChart(...)

In [238]:
covid_reports_for_day.columns

Index(['FIPS', 'Admin2', 'Province_State', 'Country_Region', 'Last_Update',
       'Lat', 'Long_', 'Confirmed', 'Deaths', 'Recovered', 'Active',
       'Combined_Key'],
      dtype='object')

In [242]:
projections = 'equirectangular'

pontos = alt.Chart(covid_reports_for_day).mark_circle(color='#FE2E2E').encode(
    longitude="Long_:Q",
    latitude="Lat:Q",
    size = size,
    tooltip = ['Confirmed:N', 'Deaths', 'Recovered', 'Province_State', 'Country_Region', 'Last_Update']
)

# Data generators for the background
sphere = alt.sphere()
graticule = alt.graticule()

# Source of land data
source = alt.topo_feature(data.world_110m.url, 'countries')

# Layering and configuring the components
teste = alt.layer(
    alt.Chart(sphere).mark_geoshape(fill='lightblue'),
    alt.Chart(graticule).mark_geoshape(stroke='white', strokeWidth=0.1),
    alt.Chart(source).mark_geoshape(fill='ForestGreen', stroke='black')
).project(
    'naturalEarth1'
).properties(width=600, height=400).configure_view(stroke=None)
    
teste + pontos    

alt.LayerChart(...)

In [18]:
alt.Chart(covid_serie_temporal).transform_fold(
    ['mortes', 'recuperacao', 'confirmacao'],
    as_=['variable', 'value']
).mark_line().encode(
    alt.X('data:T', title=''),
    alt.Y('value:Q', title='', stack=None),
    alt.Color('variable:N', 
              scale=alt.Scale(domain=['mortes', 'recuperacao', 'confirmacao'],
                              range=['red', 'green', 'yellow'])),
    order=alt.Order('variable:N', sort= 'ascending')
).properties(
    width=800,
    height=200,
    background='white'
).interactive()


alt.Chart(...)

In [232]:
teste = covid_serie_temporal.melt('data', value_vars=['mortes', 'recuperacao', 'confirmacao'], var_name = 'tipos', value_name = 'quantidade')
teste.head()

data   tipos  quantidade
0 2020-01-22  mortes        17.0
1 2020-01-23  mortes        18.0
2 2020-01-24  mortes        26.0
3 2020-01-25  mortes        42.0
4 2020-01-26  mortes        56.0

In [420]:
source = alt.topo_feature(data.world_110m.url, 'countries')

projections = 'equirectangular'

size = alt.Size('Confirmed:N', legend=None)

circles = alt.Chart(covid_reports_for_day).mark_circle(color='#FE2E2E', opacity = 0.4).encode(
    longitude="Long_:Q",
    latitude="Lat:Q",
    size = size,
    tooltip = ['Confirmed:N', 'Deaths', 'Recovered', 'Province_State', 'Country_Region', 'Last_Update']
)

geo_shape = alt.layer(
    alt.Chart(sphere).mark_geoshape(fill='lightblue', stroke = "invert ? '#777' : '#bbb'"),
    alt.Chart(graticule).mark_geoshape(stroke='white', strokeWidth=0),
    alt.Chart(source).mark_geoshape(fill='#F5F3A6', stroke='black') 
).properties(
    width=800,
    height=400
).project(projections).properties(title='Mapa mundi')

fig = alt.layer(
    geo_shape,
    circles,
)

fig.save('plots/chart.html')

fig

alt.LayerChart(...)

In [313]:

from vega_datasets import data

cars = data.cars.url

In [314]:
scales = alt.selection_interval(bind='scales')

alt.Chart(cars).mark_point().encode(
    x='Horsepower:Q',
    y='Miles_per_Gallon:Q',
    color='Origin:N'
).add_selection(
    scales
)

alt.Chart(...)

In [330]:
scales = alt.selection_interval(bind='scales')

pontos = alt.Chart(covid_reports_for_day).mark_point(opacity=0.3).encode(
    x="Long_:Q",
    y="Lat:Q",
    color = 'count(Country_Region):N'
).add_selection(
    scales
)

pontos

alt.Chart(...)

In [393]:
scales = alt.selection_interval(bind='scales')
source = alt.topo_feature(data.world_110m.url, 'countries')

projections = 'equirectangular'

size = alt.Size('Confirmed:N', legend=None)

pontos = alt.Chart(covid_reports_for_day).mark_circle(color='#FE2E2E').encode(
    x="Long_:Q",
    y="Lat:Q",
    size = size,
    tooltip = ['Confirmed:N', 'Deaths', 'Recovered', 'Province_State', 'Country_Region', 'Last_Update']
).add_selection(
    scales
)

base = alt.Chart(source).mark_geoshape(
    stroke='smolke',
).properties(
    width=800,
    height=400
).project(projections).properties(title='Mapa mundi')


base | pontos

alt.HConcatChart(...)